# SCB10X - TRANLSLATE DATA
- using selenium to collect data for free instead of API

In [88]:
import os

DATA_DIR = './data/'
SPLIT_DIR = './split_data/'
RESULT_DIR = './result/'
TRANS_DIR = './trans_data/'
driver_path = '/usr/local/bin/chromedriver'

## Split dataframe
- Separate them into 10k rows per file in `.xlsx` format

In [66]:
import pandas as pd
from glob import glob
from tqdm import tqdm
from joblib import Parallel, delayed
import os

# Get all file location
file_list = glob(os.path.join(DATA_DIR, '*'))

def split_file(path, sub_length=10000):
    name = path.split('/')[-1].split('.')[0]

    df = pd.read_csv(path)
    df['value'] = df['value'].apply(lambda text: text.encode('unicode_escape').decode('utf-8'))
    length = len(df)
    num_files = length // sub_length
    for i in range(num_files):
        sub_df = pd.DataFrame(df.loc[i*sub_length:(i+1)*sub_length-1, 'value'])
        sub_df.to_excel(os.path.join(SPLIT_DIR, f'{name}-{i}.xlsx'), index=False)
    if length%sub_length != 0:
        sub_df = pd.DataFrame(df.loc[num_files*sub_length:, 'value'])
        sub_df.to_excel(os.path.join(SPLIT_DIR, f'{name}-{num_files}.xlsx'), index=False)

In [87]:
for path in file_list:
    name = path.split('/')[-1].split('.')[0]
    print(name, len(pd.read_csv(path)))

llava_instruct_80k 442666
llava_instruct_150k 722822
conversation_58k 513740
detail_23k 46480
complex_reasoning_77k 153286


In [67]:
for path in tqdm(file_list):
    split_file(path)

100%|██████████| 5/5 [00:55<00:00, 11.16s/it]


In [68]:
len(glob(os.path.join(SPLIT_DIR, '*')))

191

## Combine DataFrame

In [134]:
import re

def sort_by_number(text):
    number = text.split('-')[-1].split('.')[0]
    return int(number)

def combine_df(path):
    name = path.split('/')[-1].split('.')[0]
    trans_list = glob(os.path.join(TRANS_DIR, name+'*'))
    trans_list = sorted(trans_list, key=sort_by_number)
    raw_df = pd.read_csv(path)
    trans_data = []
    for i, trans_path in enumerate(trans_list):
        df = pd.read_excel(trans_path)
        if i+1 < len(trans_list):           # 🚨 REMOVE THIS for New version of code
            df = df.drop(df.index[-1])      # 🚨 REMOVE THIS for New version of code
        trans_data.append(df)

    trans_df = pd.concat(trans_data, ignore_index=False).reset_index(drop=True)
    trans_df.rename(columns={'ค่า': 'translate_value'}, inplace=True)

    combine_df = pd.concat([raw_df, trans_df], axis=1)
    print(f'Finish {name}: {len(combine_df)} rows')
    combine_df.to_csv(os.path.join(RESULT_DIR, name+'.csv'))

file_list = glob(os.path.join(DATA_DIR, '*'))
for path in tqdm(file_list):
    combine_df(path)

  0%|          | 0/5 [00:00<?, ?it/s]

Finish llava_instruct_80k: 442666 rows


 20%|██        | 1/5 [00:15<01:03, 15.77s/it]

Finish llava_instruct_150k: 722822 rows


 40%|████      | 2/5 [00:42<01:06, 22.28s/it]

...

 60%|██████    | 3/5 [00:58<00:38, 19.20s/it]

Finish detail_23k: 46480 rows


 80%|████████  | 4/5 [01:00<00:12, 12.45s/it]

Finish complex_reasoning_77k: 153286 rows


100%|██████████| 5/5 [01:08<00:00, 13.77s/it]


## Check Image ID

In [151]:
import pandas as pd
trans_df = pd.read_csv('/Users/senmeetechin/Desktop/scb10x/result/detail_23k.csv')
trans_df.head()

Unnamed: 0      id             image   from  \
0           0  442786  000000442786.jpg  human   
1           1  442786  000000442786.jpg    gpt   
2           2  539056  000000539056.jpg  human   
3           3  539056  000000539056.jpg    gpt   
4           4  131697  000000131697.jpg  human   

                                               value  \
0          What do you see happening in this image?    
1  The scene depicts a lively plaza area with sev...   
2   What do you think is going on in this snapshot?    
3  The image displays a tidy home office desk set...   
4  Can you elaborate on the elements of the pictu...   

                                     translate_value  
0                       คุณเห็นอะไรเกิดขึ้นในภาพนี้?  
1   ฉากนี้แสดงให้เห็นบริเวณพลาซ่าอันมีชีวิตชีวาที...  
2                   คุณคิดว่าเกิดอะไรขึ้นในภาพรวมนี้  
3  รูปภาพแสดงการจัดโต๊ะทำงานในบ้านที่เป็นระเบียบเ...  
4   คุณช่วยอธิบายองค์ประกอบของรูปภาพที่ให้มาอย่าง...

In [156]:
df = pd.read_csv('/Users/senmeetechin/Downloads/Train_GCC-training.tsv',
                  sep='\t', 
                  names=["caption", "path"])

In [157]:
df.head()

caption  \
0                         a very typical bus station   
1  sierra looked stunning in this top and this sk...   
2  young confused girl standing in front of a war...   
3  interior design of modern living room with fir...   
4    cybernetic scene isolated on white background .   

                                                path  
0  http://lh6.ggpht.com/-IvRtNLNcG8o/TpFyrudaT6I/...  
1  http://78.media.tumblr.com/3b133294bdc7c7784b7...  
2  https://media.gettyimages.com/photos/young-con...  
3  https://thumb1.shutterstock.com/display_pic_wi...  
4  https://thumb1.shutterstock.com/display_pic_wi...

In [158]:
df.loc[442785, 'path']

'http://wpmedia.ottawacitizen.com/2014/09/jacqui-du-toit-reads-a-poster-at-the-ottawa-school-of-art-w1.jpg?quality=55&strip=all'

In [161]:
df.loc[442787, 'path']

'https://thumb7.shutterstock.com/display_pic_with_logo/326929/772024501/stock-vector-square-winter-background-with-snowflakes-and-christmas-decorations-beautiful-layout-for-a-greeting-772024501.jpg'

## Check Metadata

In [178]:
import json
import pandas as pd

with open('/Users/senmeetechin/Downloads/metadata.json') as f:
    data = json.load(f)
meta_df = pd.DataFrame(data)
print(len(meta_df))
meta_df.head()

595375


id                    image  \
0  GCC_train_002582585  GCC_train_002582585.jpg   
1  GCC_train_002429825  GCC_train_002429825.jpg   
2  GCC_train_000190697  GCC_train_000190697.jpg   
3  GCC_train_002503829  GCC_train_002503829.jpg   
4  GCC_train_000530863  GCC_train_000530863.jpg   

                                             caption  \
0  olive oil is a healthy ingredient used liberal...   
1  3d vector deluxe alphabet of randomly rotated ...   
2  weathering -- the physical & chemical breakdow...   
3  fans interferes with # on a ball hit by # of s...   
4          train that takes you around the perimeter   

                                        blip_caption  \
0          some olive oil and salt in a glass bottle   
1  the number three thousand gold on a dark backg...   
2                                               None   
3                                               None   
4                         the train ride at the park   

                                                 url  
0  https://i.pinimg.com/736x/de/13/3a/de133a155c7...  
1  https://thumb9.shutterstock.com/display_pic_wi...  
2  http://slideplayer.com/9374162/28/images/2/Wea...  
3  https://media.gettyimages.com/photos/fans-inte...  
4  https://media-cdn.tripadvisor.com/media/photo-...

In [177]:
from glob import glob
from tqdm import tqdm

csv_list = glob('./result/*.csv')

img_list = []
for path in tqdm(csv_list):
    df = pd.read_csv(path)
    img = list(df['image'])
    img_list += img

img_all = list(set(img_list))
len(img_list), len(img_all)

(1878994, 81479)

### Check VQA with images.zip

In [180]:
file_list = glob('/Users/senmeetechin/Downloads/images/*')
len(file_list)

595375

In [198]:
# Check VQA with image from images.zip
id_set = set([img.split('_')[-1] for img in tqdm(file_list)])
not_have = list(set(img_all) - id_set)
len(not_have)

100%|██████████| 595375/595375 [00:00<00:00, 2959341.08it/s]


81479

### Check VQA with metadata.json

In [207]:
meta_img_list = list(meta_df['image'])
meta_id_set = [name.split('_')[-1] for name in meta_img_list]
not_have = list(set(img_all) - set(meta_id_set))
len(not_have)

81479

In [211]:
with open('/Users/senmeetechin/Downloads/chat.json') as f:
    data = json.load(f)
chat_df = pd.DataFrame(data)
chat_df.head()

id                    image  \
0  GCC_train_002582585  GCC_train_002582585.jpg   
1  GCC_train_002429825  GCC_train_002429825.jpg   
2  GCC_train_000190697  GCC_train_000190697.jpg   
3  GCC_train_002503829  GCC_train_002503829.jpg   
4  GCC_train_000530863  GCC_train_000530863.jpg   

                                       conversations  
0  [{'from': 'human', 'value': 'Provide a brief d...  
1  [{'from': 'human', 'value': '<image>
Write a t...  
2  [{'from': 'human', 'value': 'Share a concise i...  
3  [{'from': 'human', 'value': 'Relay a brief, cl...  
4  [{'from': 'human', 'value': '<image>
Render a ...

## NEW

In [236]:
import os

DATA_DIR = './data/'
SPLIT_DIR = './split_data/'
RESULT_DIR = './result/'
TRANS_DIR = './trans_data/'

In [239]:
import pandas as pd
from glob import glob
from tqdm import tqdm
from joblib import Parallel, delayed
import os

# Get all file location
file_list = glob(os.path.join(DATA_DIR, '*'))

def split_file(path, sub_length=10000):
    name = path.split('/')[-1].split('.')[0]

    df = pd.read_csv(path)
    df['value'] = df['value'].astype('str')
    df['value'] = df['value'].apply(lambda text: text.encode('unicode_escape').decode('utf-8'))
    length = len(df)
    num_files = length // sub_length
    for i in tqdm(range(num_files)):
        sub_df = pd.DataFrame(df.loc[i*sub_length:(i+1)*sub_length-1, 'value'])
        sub_df.to_excel(os.path.join(SPLIT_DIR, f'{name}-{i}.xlsx'), index=False)
    if length%sub_length != 0:
        sub_df = pd.DataFrame(df.loc[num_files*sub_length:, 'value'])
        sub_df.to_excel(os.path.join(SPLIT_DIR, f'{name}-{num_files}.xlsx'), index=False)

In [240]:
split_file('./data/llava_v1_5_mix665k.csv')

/var/folders/gk/_5rztwzx5bj_8n38ybbp_b280000gn/T/ipykernel_78859/727206476.py:13: DtypeWarning: Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(path)
100%|██████████| 671/671 [03:08<00:00,  3.56it/s]


In [241]:
len(glob('/Users/senmeetechin/Desktop/scb10x/split_data/*'))

672

In [242]:
import re

def sort_by_number(text):
    number = text.split('-')[-1].split('.')[0]
    return int(number)

def combine_df(path):
    name = path.split('/')[-1].split('.')[0]
    trans_list = glob(os.path.join(TRANS_DIR, name+'*'))
    trans_list = sorted(trans_list, key=sort_by_number)
    raw_df = pd.read_csv(path)
    trans_data = []
    for i, trans_path in enumerate(tqdm(trans_list)):
        df = pd.read_excel(trans_path)
        trans_data.append(df)

    trans_df = pd.concat(trans_data, ignore_index=False).reset_index(drop=True)
    trans_df.rename(columns={'ค่า': 'translate_value'}, inplace=True)

    combine_df = pd.concat([raw_df, trans_df], axis=1)
    print(f'Finish {name}: {len(combine_df)} rows')
    combine_df.to_csv(os.path.join(RESULT_DIR, name+'.csv'), index=False)

file_list = glob(os.path.join(DATA_DIR, 'llava_v1_5_mix665k*'))
for path in tqdm(file_list):
    combine_df(path)

  0%|          | 0/1 [00:00<?, ?it/s]/var/folders/gk/_5rztwzx5bj_8n38ybbp_b280000gn/T/ipykernel_78859/3692771486.py:11: DtypeWarning: Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.
  raw_df = pd.read_csv(path)
100%|██████████| 672/672 [01:59<00:00,  5.63it/s]


Finish llava_v1_5_mix665k: 6712322 rows


100%|██████████| 1/1 [02:27<00:00, 147.86s/it]


## Normal LLAVA data

In [11]:
import pandas as pd
df = pd.read_parquet('/Users/senmeetechin/Desktop/scb10x/data/chat_dis_filtered.parquet')
df.head()

id                    image   from  \
0  GCC_train_002582585  GCC_train_002582585.jpg  human   
1  GCC_train_002582585  GCC_train_002582585.jpg    gpt   
2  GCC_train_002429825  GCC_train_002429825.jpg  human   
3  GCC_train_002429825  GCC_train_002429825.jpg    gpt   
4  GCC_train_000190697  GCC_train_000190697.jpg  human   

                                               value  \
0   Provide a brief description of the given image.    
1  olive oil is a healthy ingredient used liberal...   
2   Write a terse but informative summary of the ...   
3  3d vector deluxe alphabet of randomly rotated ...   
4  Share a concise interpretation of the image pr...   

                                     translate_value  distance  
0                ระบุคำอธิบายโดยย่อของภาพที่กำหนดให้  0.161393  
1   น้ำมันมะกอกเป็นส่วนผสมที่ดีต่อสุขภาพที่ใช้กัน...  0.099871  
2                เขียนบทสรุปสั้นๆ แต่ให้ข้อมูลของภาพ  0.124710  
3   ตัวอักษรดีลักซ์เวกเตอร์ 3 ตัวของสัญลักษณ์สีทอ...  0.262322  
4                 แบ่งปันการตีความภาพที่ให้โดยกระชับ  0.136235

In [12]:
import numpy as np

df.loc[df['from']=='human', 'translate_value'] = df.loc[df['from']=='human', 'translate_value'].apply(lambda x: np.random.choice(['<image>\n'+x.strip(), x.strip()+'\n<image>']))
df['translate_value'] = df['translate_value'].apply(lambda x: x.replace('<ภาพ>', '<image>'))
df['conversations'] = df.apply(lambda x: {'from': x['from'], 'value': x['translate_value'].strip()}, axis=1)
df = df.sort_values(by=['id', 'from'], ascending=False)
df.head(10)

id                    image   from  \
665304  GCC_train_002828523  GCC_train_002828523.jpg  human   
665305  GCC_train_002828523  GCC_train_002828523.jpg    gpt   
408362  GCC_train_002828520  GCC_train_002828520.jpg  human   
408363  GCC_train_002828520  GCC_train_002828520.jpg    gpt   
2928    GCC_train_002828514  GCC_train_002828514.jpg  human   
2929    GCC_train_002828514  GCC_train_002828514.jpg    gpt   
568494  GCC_train_002828511  GCC_train_002828511.jpg  human   
568495  GCC_train_002828511  GCC_train_002828511.jpg    gpt   
428534  GCC_train_002828507  GCC_train_002828507.jpg  human   
428535  GCC_train_002828507  GCC_train_002828507.jpg    gpt   

                                                    value  \
665304  Relay a brief, clear account of the picture sh...   
665305        create your very own herb garden in a # diy   
408362  Relay a brief, clear account of the picture sh...   
408363  a few of the evening 's talented dancers pract...   
2928     Create a compact narrative representing the i...   
2929    peacock feather on the background in white colors   
568494  Create a compact narrative representing the im...   
568495                      mother and baby in a car seat   
428534   Present a compact description of the photo's ...   
428535  property image # - at the top of the world wit...   

                                          translate_value  distance  \
665304    เล่าเรื่องราวสั้นๆ ชัดเจนของภาพที่แสดง\n<image>  0.116875   
665305                    สร้างสวนสมุนไพรของคุณเองใน #diy  0.049555   
408362    เล่าเรื่องราวสั้นๆ ชัดเจนของภาพที่แสดง\n<image>  0.116875   
408363   นักเต้นที่มีพรสวรรค์สองสามคนฝึกซ้อมหน้ากระจกใ...  0.070743   
2928    สร้างการเล่าเรื่องที่มีขนาดกะทัดรัดซึ่งแสดงถึง...  0.100399   
2929                           ขนนกยูงบนพื้นหลังเป็นสีขาว  0.170985   
568494  <image>\nสร้างการเล่าเรื่องที่มีขนาดกะทัดรัดซึ...  0.100399   
568495                         แม่และลูกอยู่ในที่นั่งในรถ  0.109079   
428534  <image>\nนำเสนอคำอธิบายสั้นๆ เกี่ยวกับคุณลักษณ...  0.189725   
428535   ภาพทรัพย์สิน # - ที่สุดของโลกพร้อมวิวภูเขา อ่...  0.073936   

                                            conversations  
665304  {'from': 'human', 'value': 'เล่าเรื่องราวสั้นๆ...  
665305  {'from': 'gpt', 'value': 'สร้างสวนสมุนไพรของคุ...  
408362  {'from': 'human', 'value': 'เล่าเรื่องราวสั้นๆ...  
408363  {'from': 'gpt', 'value': 'นักเต้นที่มีพรสวรรค์...  
2928    {'from': 'human', 'value': 'สร้างการเล่าเรื่อง...  
2929    {'from': 'gpt', 'value': 'ขนนกยูงบนพื้นหลังเป็...  
568494  {'from': 'human', 'value': '<image>
สร้างการเล...  
568495  {'from': 'gpt', 'value': 'แม่และลูกอยู่ในที่นั...  
428534  {'from': 'human', 'value': '<image>
นำเสนอคำอธ...  
428535  {'from': 'gpt', 'value': 'ภาพทรัพย์สิน # - ที่...

In [13]:
filter_df = df[['id', 'image', 'conversations']]
filter_df = filter_df.groupby(['id', 'image'])['conversations'].apply(list).reset_index(name='conversations')
filter_df['conversations'][0]

[{'from': 'human', 'value': 'สรุปเนื้อหาภาพของภาพ\n<image>'},
 {'from': 'gpt', 'value': 'สถานีขนส่งทั่วไป'}]

In [15]:
filter_df.to_json('./result/chat4train-final.json', orient='records')

## LLAVA mix 665k

In [42]:
df = pd.read_csv('/Users/senmeetechin/Desktop/scb10x/result/llava_v1_5_mix665k.csv')
df.sample(10)

FileNotFoundError: [Errno 2] No such file or directory: '/Users/senmeetechin/Desktop/scb10x/result/llava_v1_5_mix665k.csv'

In [253]:
df['translate_value'] = df['translate_value'].apply(lambda x: x.replace('<ภาพ>', '<image>'))
df['conversations'] = df.apply(lambda x: {'from': x['from'], 'value': x['translate_value'].strip()}, axis=1)
df = df.sort_values(by=['id', 'order'])
df.head(10)

id             image   from  \
4613884  1  gqa/images/1.jpg  human   
4613885  1  gqa/images/1.jpg    gpt   
4613886  1  gqa/images/1.jpg  human   
4613887  1  gqa/images/1.jpg    gpt   
4613888  1  gqa/images/1.jpg  human   
4613889  1  gqa/images/1.jpg    gpt   
4613890  1  gqa/images/1.jpg  human   
4613891  1  gqa/images/1.jpg    gpt   
4613892  1  gqa/images/1.jpg  human   
4613893  1  gqa/images/1.jpg    gpt   

                                                     value  order  \
4613884  <image> Are there any parking meters on the si...      0   
4613885                                                Yes      1   
4613886  Do you see any cars to the left of the man tha...      2   
4613887                                                 No      3   
4613888            What vehicle is to the left of the van?      4   
4613889                                                Car      5   
4613890  What is the vehicle to the right of the car th...      6   
4613891                                                Van      7   
4613892    Are there any statues to the left of the clock?      8   
4613893                                                 No      9   

                                           translate_value  \
4613884   <image> มีมิเตอร์จอดรถบนทางเท้าใกล้ถนนหรือไม่...   
4613885                                                ใช่   
4613886  คุณเห็นรถทางซ้ายของผู้ชายที่อยู่ทางขวาของจักรย...   
4613887                                             เลขที่   
4613888                     รถอะไรอยู่ทางด้านซ้ายของรถตู้?   
4613889                                                 รถ   
4613890   รถที่อยู่ทางขวาของรถที่อยู่ทางขวาของจักรยานคื...   
4613891                                              รถตู้   
4613892          มีรูปปั้นอยู่ทางด้านซ้ายของนาฬิกาหรือไม่?   
4613893                                             เลขที่   

                                             conversations  
4613884  {'from': 'human', 'value': '<image> มีมิเตอร์จ...  
4613885                    {'from': 'gpt', 'value': 'ใช่'}  
4613886  {'from': 'human', 'value': 'คุณเห็นรถทางซ้ายขอ...  
4613887                 {'from': 'gpt', 'value': 'เลขที่'}  
4613888  {'from': 'human', 'value': 'รถอะไรอยู่ทางด้านซ...  
4613889                     {'from': 'gpt', 'value': 'รถ'}  
4613890  {'from': 'human', 'value': 'รถที่อยู่ทางขวาของ...  
4613891                  {'from': 'gpt', 'value': 'รถตู้'}  
4613892  {'from': 'human', 'value': 'มีรูปปั้นอยู่ทางด้...  
4613893                 {'from': 'gpt', 'value': 'เลขที่'}

In [254]:
filter_df = df[['id', 'image', 'conversations']]
filter_df = filter_df.groupby(['id', 'image'])['conversations'].apply(list).reset_index(name='conversations')
filter_df['conversations'][0]

[{'from': 'human',
  'value': '<image> มีมิเตอร์จอดรถบนทางเท้าใกล้ถนนหรือไม่? ตอบคำถามโดยใช้คำหรือวลีเดียว'},
 {'from': 'gpt', 'value': 'ใช่'},
 {'from': 'human',
  'value': 'คุณเห็นรถทางซ้ายของผู้ชายที่อยู่ทางขวาของจักรยานบ้างไหม?'},
 {'from': 'gpt', 'value': 'เลขที่'},
 {'from': 'human', 'value': 'รถอะไรอยู่ทางด้านซ้ายของรถตู้?'},
 {'from': 'gpt', 'value': 'รถ'},
 {'from': 'human',
  'value': 'รถที่อยู่ทางขวาของรถที่อยู่ทางขวาของจักรยานคือรถอะไร?'},
 {'from': 'gpt', 'value': 'รถตู้'},
 {'from': 'human', 'value': 'มีรูปปั้นอยู่ทางด้านซ้ายของนาฬิกาหรือไม่?'},
 {'from': 'gpt', 'value': 'เลขที่'},
 {'from': 'human', 'value': 'ทางเท้าทำมาจากอะไร?'},
 {'from': 'gpt', 'value': 'อิฐ'},
 {'from': 'human', 'value': 'รถอะไรจอดอยู่ริมถนนใกล้ทางเท้า?'},
 {'from': 'gpt', 'value': 'รถตู้'},
 {'from': 'human', 'value': 'รองเท้ามีสีน้ำตาลหรือสีเขียว?'},
 {'from': 'gpt', 'value': 'สีน้ำตาล'},
 {'from': 'human', 'value': 'แก้วอยู่ทางขวาของตู้เย็นใช่ไหม?'},
 {'from': 'gpt', 'value': 'เลขที่'},
 {'from':

In [255]:
filter_df.to_json('./result/llava_v1_5_mix665k_translate.json', orient='records')

In [257]:
import json

with open('./result/llava_v1_5_mix665k-translate.json') as f:
    data = json.load(f)
data

[{'id': 1,
  'image': 'gqa/images/1.jpg',
  'conversations': [{'from': 'human',
    'value': '<image> มีมิเตอร์จอดรถบนทางเท้าใกล้ถนนหรือไม่? ตอบคำถามโดยใช้คำหรือวลีเดียว'},
   {'from': 'gpt', 'value': 'ใช่'},
   {'from': 'human',
    'value': 'คุณเห็นรถทางซ้ายของผู้ชายที่อยู่ทางขวาของจักรยานบ้างไหม?'},
   {'from': 'gpt', 'value': 'เลขที่'},
   {'from': 'human', 'value': 'รถอะไรอยู่ทางด้านซ้ายของรถตู้?'},
   {'from': 'gpt', 'value': 'รถ'},
   {'from': 'human',
    'value': 'รถที่อยู่ทางขวาของรถที่อยู่ทางขวาของจักรยานคือรถอะไร?'},
   {'from': 'gpt', 'value': 'รถตู้'},
   {'from': 'human', 'value': 'มีรูปปั้นอยู่ทางด้านซ้ายของนาฬิกาหรือไม่?'},
   {'from': 'gpt', 'value': 'เลขที่'},
   {'from': 'human', 'value': 'ทางเท้าทำมาจากอะไร?'},
   {'from': 'gpt', 'value': 'อิฐ'},
   {'from': 'human', 'value': 'รถอะไรจอดอยู่ริมถนนใกล้ทางเท้า?'},
   {'from': 'gpt', 'value': 'รถตู้'},
   {'from': 'human', 'value': 'รองเท้ามีสีน้ำตาลหรือสีเขียว?'},
   {'from': 'gpt', 'value': 'สีน้ำตาล'},
   {'from': '

## RE DATASET

In [120]:
import pandas as pd
df = pd.read_csv('/Users/senmeetechin/Desktop/scb10x/result/llava_v1_5_mix665k-translate.csv')
df

/var/folders/gk/_5rztwzx5bj_8n38ybbp_b280000gn/T/ipykernel_38304/3861197245.py:2: DtypeWarning: Columns (0) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv('/Users/senmeetechin/Desktop/scb10x/result/llava_v1_5_mix665k-translate.csv')


id                                      image   from  \
0                   33471            coco/train2017/000000033471.jpg  human   
1                   33471            coco/train2017/000000033471.jpg    gpt   
2                   33471            coco/train2017/000000033471.jpg  human   
3                   33471            coco/train2017/000000033471.jpg    gpt   
4                   33471            coco/train2017/000000033471.jpg  human   
...                   ...                                        ...    ...   
6712317  07c44727285d8060  textvqa/train_images/07c44727285d8060.jpg    gpt   
6712318  bd75fd0264fdaf5b  textvqa/train_images/bd75fd0264fdaf5b.jpg  human   
6712319  bd75fd0264fdaf5b  textvqa/train_images/bd75fd0264fdaf5b.jpg    gpt   
6712320  4508de4f680374a7  textvqa/train_images/4508de4f680374a7.jpg  human   
6712321  4508de4f680374a7  textvqa/train_images/4508de4f680374a7.jpg    gpt   

                                                     value  order  \
0        <image> What are the colors of the bus in the ...      0   
1                   The bus in the image is white and red.      1   
2         What feature can be seen on the back of the bus?      2   
3           The back of the bus features an advertisement.      3   
4        Is the bus driving down the street or pulled o...      4   
...                                                    ...    ...   
6712317  The pages of opened book is arranged ina heart...      1   
6712318  <image> Provide a one-sentence caption for the...      0   
6712319  A sketch of a man in behind the counter in a b...      1   
6712320  <image> Provide a one-sentence caption for the...      0   
6712321  A picture of a fridge, with no discernible tex...      1   

                                           translate_value  
0                              <image> รถบัสในภาพมีสีอะไร?  
1                                  รถเมล์ในภาพเป็นสีขาวแดง  
2                        ด้านหลังรถบัสมีคุณลักษณะอะไรบ้าง?  
3                                 ด้านหลังรถบัสมีป้ายโฆษณา  
4           รถบัสกำลังวิ่งไปตามถนนหรือถูกดึงออกไปด้านข้าง?  
...                                                    ...  
6712317  หน้าหนังสือที่เปิดอยู่จัดเรียงเป็นรูปหัวใจ แต่...  
6712318   <image> ระบุคำบรรยายหนึ่งประโยคสำหรับรูปภาพที...  
6712319   ภาพร่างของชายคนหนึ่งที่อยู่หลังเคาน์เตอร์ในร้...  
6712320   <image> ระบุคำบรรยายหนึ่งประโยคสำหรับรูปภาพที...  
6712321       รูปภาพตู้เย็นที่ไม่มีข้อความชัดเจนอยู่ในนั้น  

[6712322 rows x 6 columns]

In [121]:
filter_out = list(set(df[df.value.isna()]['id']))
len(filter_out)

1350

In [122]:
filter_df = df[~df.id.isin(filter_out)]
filter_df

id                                      image   from  \
0                   33471            coco/train2017/000000033471.jpg  human   
1                   33471            coco/train2017/000000033471.jpg    gpt   
2                   33471            coco/train2017/000000033471.jpg  human   
3                   33471            coco/train2017/000000033471.jpg    gpt   
4                   33471            coco/train2017/000000033471.jpg  human   
...                   ...                                        ...    ...   
6712317  07c44727285d8060  textvqa/train_images/07c44727285d8060.jpg    gpt   
6712318  bd75fd0264fdaf5b  textvqa/train_images/bd75fd0264fdaf5b.jpg  human   
6712319  bd75fd0264fdaf5b  textvqa/train_images/bd75fd0264fdaf5b.jpg    gpt   
6712320  4508de4f680374a7  textvqa/train_images/4508de4f680374a7.jpg  human   
6712321  4508de4f680374a7  textvqa/train_images/4508de4f680374a7.jpg    gpt   

                                                     value  order  \
0        <image> What are the colors of the bus in the ...      0   
1                   The bus in the image is white and red.      1   
2         What feature can be seen on the back of the bus?      2   
3           The back of the bus features an advertisement.      3   
4        Is the bus driving down the street or pulled o...      4   
...                                                    ...    ...   
6712317  The pages of opened book is arranged ina heart...      1   
6712318  <image> Provide a one-sentence caption for the...      0   
6712319  A sketch of a man in behind the counter in a b...      1   
6712320  <image> Provide a one-sentence caption for the...      0   
6712321  A picture of a fridge, with no discernible tex...      1   

                                           translate_value  
0                              <image> รถบัสในภาพมีสีอะไร?  
1                                  รถเมล์ในภาพเป็นสีขาวแดง  
2                        ด้านหลังรถบัสมีคุณลักษณะอะไรบ้าง?  
3                                 ด้านหลังรถบัสมีป้ายโฆษณา  
4           รถบัสกำลังวิ่งไปตามถนนหรือถูกดึงออกไปด้านข้าง?  
...                                                    ...  
6712317  หน้าหนังสือที่เปิดอยู่จัดเรียงเป็นรูปหัวใจ แต่...  
6712318   <image> ระบุคำบรรยายหนึ่งประโยคสำหรับรูปภาพที...  
6712319   ภาพร่างของชายคนหนึ่งที่อยู่หลังเคาน์เตอร์ในร้...  
6712320   <image> ระบุคำบรรยายหนึ่งประโยคสำหรับรูปภาพที...  
6712321       รูปภาพตู้เย็นที่ไม่มีข้อความชัดเจนอยู่ในนั้น  

[6647006 rows x 6 columns]

In [88]:
df = filter_df.copy()
df['translate_value'] = df['translate_value'].apply(lambda x: x.replace('<ภาพ>', '<image>'))
df['conversations'] = df.apply(lambda x: {'from': x['from'], 'value': x['translate_value'].strip()}, axis=1)
df = df.sort_values(by=['id', 'order'])
df.head(10)

id             image   from  \
5482566  3  gqa/images/3.jpg  human   
5482567  3  gqa/images/3.jpg    gpt   
5482568  3  gqa/images/3.jpg  human   
5482569  3  gqa/images/3.jpg    gpt   
5482570  3  gqa/images/3.jpg  human   
5482571  3  gqa/images/3.jpg    gpt   
5482572  3  gqa/images/3.jpg  human   
5482573  3  gqa/images/3.jpg    gpt   
5482574  3  gqa/images/3.jpg  human   
5482575  3  gqa/images/3.jpg    gpt   

                                                     value  order  \
5482566  <image> Which kind of furniture is not white? ...      0   
5482567                                             Drawer      1   
5482568                  Which kind of furniture is white?      2   
5482569                                              Table      3   
5482570                        Are there any black phones?      4   
5482571                                                Yes      5   
5482572       Are there both bags and phones in the photo?      6   
5482573                                                Yes      7   
5482574                       On which side is the drawer?      8   
5482575                                               Left      9   

                                           translate_value  \
5482566  <image> เฟอร์นิเจอร์แบบไหนที่ไม่ขาว? ตอบคำถามโ...   
5482567                                            ลิ้นชัก   
5482568                 เฟอร์นิเจอร์ประเภทไหนที่เป็นสีขาว?   
5482569                                               โต๊ะ   
5482570                             มีโทรศัพท์สีดำบ้างไหม?   
5482571                                                ใช่   
5482572               ในรูปมีทั้งกระเป๋าและโทรศัพท์มั้ยคะ?   
5482573                                                ใช่   
5482574                                ลิ้นชักอยู่ด้านไหน?   
5482575                                               ซ้าย   

                                             conversations  
5482566  {'from': 'human', 'value': '<image> เฟอร์นิเจอ...  
5482567                {'from': 'gpt', 'value': 'ลิ้นชัก'}  
5482568  {'from': 'human', 'value': 'เฟอร์นิเจอร์ประเภท...  
5482569                   {'from': 'gpt', 'value': 'โต๊ะ'}  
5482570  {'from': 'human', 'value': 'มีโทรศัพท์สีดำบ้าง...  
5482571                    {'from': 'gpt', 'value': 'ใช่'}  
5482572  {'from': 'human', 'value': 'ในรูปมีทั้งกระเป๋า...  
5482573                    {'from': 'gpt', 'value': 'ใช่'}  
5482574  {'from': 'human', 'value': 'ลิ้นชักอยู่ด้านไหน?'}  
5482575                   {'from': 'gpt', 'value': 'ซ้าย'}

In [89]:
filter_df = df[['id', 'image', 'conversations']]
filter_df = filter_df.groupby(['id', 'image'])['conversations'].apply(list).reset_index(name='conversations')
filter_df['conversations'][0]

[{'from': 'human',
  'value': '<image> เฟอร์นิเจอร์แบบไหนที่ไม่ขาว? ตอบคำถามโดยใช้คำหรือวลีเดียว'},
 {'from': 'gpt', 'value': 'ลิ้นชัก'},
 {'from': 'human', 'value': 'เฟอร์นิเจอร์ประเภทไหนที่เป็นสีขาว?'},
 {'from': 'gpt', 'value': 'โต๊ะ'},
 {'from': 'human', 'value': 'มีโทรศัพท์สีดำบ้างไหม?'},
 {'from': 'gpt', 'value': 'ใช่'},
 {'from': 'human', 'value': 'ในรูปมีทั้งกระเป๋าและโทรศัพท์มั้ยคะ?'},
 {'from': 'gpt', 'value': 'ใช่'},
 {'from': 'human', 'value': 'ลิ้นชักอยู่ด้านไหน?'},
 {'from': 'gpt', 'value': 'ซ้าย'},
 {'from': 'human', 'value': 'อุปกรณ์อะไรอยู่บนโต๊ะ?'},
 {'from': 'gpt', 'value': 'โทรศัพท์'},
 {'from': 'human', 'value': 'ใครอยู่หน้าคอมพิวเตอร์ทางด้านขวา?'},
 {'from': 'gpt', 'value': 'สาว'},
 {'from': 'human', 'value': 'ผู้หญิงที่อยู่ข้างหน้าคืออุปกรณ์อะไร?'},
 {'from': 'gpt', 'value': 'คอมพิวเตอร์'},
 {'from': 'human', 'value': 'ผู้หญิงตรงหน้าคืออะไร?'},
 {'from': 'gpt', 'value': 'คอมพิวเตอร์'},
 {'from': 'human', 'value': 'คุณเห็นเครื่องคิดเลขใกล้ปากกาไหม?'},
 {'from': 'g

In [90]:
filter_df.to_json('./result/llava_v1_5_mix665k_translate-doubleHuman.json', orient='records')

In [91]:
import json

with open('/Users/senmeetechin/Desktop/scb10x/result/llava_v1_5_mix665k_translate-doubleHuman.json') as f:
    data = json.load(f)
len(data)

174562

In [92]:
import json

with open('/Users/senmeetechin/Desktop/scb10x/result/llava_v1_5_mix665k_translate-filterNaN.json') as f:
    data = json.load(f)
len(data)

357351

In [106]:
import json

with open('/Users/senmeetechin/Desktop/scb10x/data/llava_v1_5_mix665k.json') as f:
    data = json.load(f)
data[0]

{'id': '000000033471',
 'image': 'coco/train2017/000000033471.jpg',
 'conversations': [{'from': 'human',
   'value': '<image>\nWhat are the colors of the bus in the image?'},
  {'from': 'gpt', 'value': 'The bus in the image is white and red.'},
  {'from': 'human',
   'value': 'What feature can be seen on the back of the bus?'},
  {'from': 'gpt', 'value': 'The back of the bus features an advertisement.'},
  {'from': 'human',
   'value': 'Is the bus driving down the street or pulled off to the side?'},
  {'from': 'gpt',
   'value': 'The bus is driving down the street, which is crowded with people and other vehicles.'}]}

In [113]:
df = df[df['translate_value'].apply(lambda x: '<ภาพ>' in x)]
df['translate_value'] = df['translate_value'].apply(lambda x: x.replace('<ภาพ>', '<image>'))
df

/var/folders/gk/_5rztwzx5bj_8n38ybbp_b280000gn/T/ipykernel_38304/48901796.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['translate_value'] = df['translate_value'].apply(lambda x: x.replace('<ภาพ>', '<image>'))


id                            image   from  \
6          52846  coco/train2017/000000052846.jpg  human   
34        398214  coco/train2017/000000398214.jpg  human   
62         87286  coco/train2017/000000087286.jpg  human   
80        175217  coco/train2017/000000175217.jpg  human   
90        230238  coco/train2017/000000230238.jpg  human   
...          ...                              ...    ...   
5895478     3738              gqa/images/3738.jpg  human   
5895810  2333128           gqa/images/2333128.jpg  human   
5895874  2416853           gqa/images/2416853.jpg  human   
5895954  1592660           gqa/images/1592660.jpg  human   
5896072  2337260           gqa/images/2337260.jpg  human   

                                                     value  order  \
6        Where is the cat positioned in the image? <image>      0   
34       What type of sign and traffic device can be se...      0   
62       What is hanging from the traffic light pole? <...      0   
80       What is the color of the sink and vanity in th...      0   
90       <image> What is the main color of the vase in ...      0   
...                                                    ...    ...   
5895478  <image> Is there a fire hydrant or a helmet in...      0   
5895810  <image> Are there either microphones or camera...      0   
5895874  <image> Are there either any desk lamps or not...      0   
5895954  <image> Is there either a fence or a helmet in...      0   
5896072  <image> Are there any frisbees or mats in the ...      0   

                                           translate_value  
6                         แมวอยู่ในตำแหน่งใดในภาพ? <image>  
34          ในภาพจะเห็นป้ายและอุปกรณ์จราจรประเภทใด <image>  
62                      อะไรห้อยลงมาจากเสาไฟจราจร? <image>  
80        อ่างล้างหน้าและโต๊ะเครื่องแป้งในห้องน้ำมีสีอะ...  
90                            <image> แจกันในภาพคือสีอะไร?  
...                                                    ...  
5895478   <image> ในรูปมีหัวจ่ายน้ำดับเพลิงหรือหมวกกันน...  
5895810   <image> มีไมโครโฟนหรือกล้องอยู่ในภาพหรือไม่? ...  
5895874   <image> มีโคมไฟตั้งโต๊ะหรือกระดาษจดบันทึกอยู่...  
5895954   <image> ในรูปมีรั้วหรือหมวกกันน็อคมั้ย? ตอบคำ...  
5896072   <image> มีจานร่อนหรือเสื่ออยู่ในภาพบ้างไหม? ต...  

[92362 rows x 6 columns]